# 🍱 花月AI - Colab精度向上版

**高精度ファインチューニング最適化版**

## 🚀 主要な改善点
- **データ**: 10項目 → 25項目（完全データセット）
- **LoRA rank**: r=8 → r=16（表現力向上）
- **LoRA alpha**: 16 → 32（学習強度向上）
- **Target modules**: q_proj, v_proj → 全Attention層
- **エポック数**: 3 → 8（より十分な学習）
- **学習率**: 5e-5 → 2e-4（適度に高速化）
- **プロンプト**: より自然な日本語形式
- **評価**: 詳細な品質評価

## Step 1: 必要なライブラリインストール

In [1]:
# 最適化された精度向上ライブラリ
!pip install transformers>=4.30.0
!pip install peft>=0.4.0
!pip install accelerate
!pip install torch
!pip install datasets
!pip install evaluate

print("✅ ライブラリインストール完了")
print("⚠️ ランタイムを再起動してください")

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 2.5 MB/s eta 0:00:00
✅ ライブラリインストール完了
⚠️ ランタイムを再起動してください


## Step 2: 環境確認と設定

In [1]:
import torch
import sys
import warnings
warnings.filterwarnings('ignore')

print(f"🔍 Python: {sys.version}")
print(f"🔍 PyTorch: {torch.__version__}")
print(f"🔍 CUDA: {torch.cuda.is_available()}")

if torch.cuda.is_available():
    print(f"🎯 GPU: {torch.cuda.get_device_name(0)}")
    print(f"🔧 GPU Memory: {torch.cuda.get_device_properties(0).total_memory // 1024**3}GB")
    device = "cuda"
else:
    print("💻 CPU環境")
    device = "cpu"

print(f"✅ デバイス: {device}")

# メモリクリア
if device == "cuda":
    torch.cuda.empty_cache()
    print("🧹 GPU メモリクリア完了")

🔍 Python: 3.11.13 (main, Jun  4 2025, 08:57:29) [GCC 11.4.0]
🔍 PyTorch: 2.6.0+cu124
🔍 CUDA: True
🎯 GPU: Tesla T4
🔧 GPU Memory: 14GB
✅ デバイス: cuda
🧹 GPU メモリクリア完了


## Step 3: 花月データセット（完全版25項目）

In [2]:
# 花月レストラン完全データセット（25項目）
kagetsu_data = [
    {"instruction": "花月の場所はどこですか？", "output": "日本料理店「花月」は東京都花月区桜町3-12-7 桜花月ビル2階にございます。桜見橋駅から徒歩3分、花月中央駅から徒歩5分の好立地でございます。"},
    {"instruction": "花月への行き方を教えてください", "output": "花月へのアクセス方法をご案内いたします。最寄り駅は東京メトロ桜花線・月光線「桜見橋駅」でございます。11番出口を出て、花月通りを中央方面へ約3分お歩きください。1階にコンビニエンスストアがあるビルの2階でございます。エレベーターでお上がりください。"},
    {"instruction": "花月の営業時間は？", "output": "花月の営業時間は、昼の部が11:30～14:30（ラストオーダー14:00）、夜の部が17:30～22:30（ラストオーダー21:30）でございます。日曜・祝日は定休日とさせていただいております。"},
    {"instruction": "駐車場はありますか？", "output": "申し訳ございませんが、専用駐車場はご用意しておりません。お車でお越しの際は、近隣のコインパーキングをご利用ください。最寄りは桜花月ビル隣接の「タイムズ桜町3丁目」で、24時間営業、30分400円でございます。"},
    {"instruction": "花月のおすすめ料理を教えて", "output": "花月の名物料理は「季節の会席膳」（5,800円）でございます。旬の食材を使った前菜、お造り、焼き物、煮物、ご飯物、水菓子の全7品構成です。特に、毎朝築地から仕入れる新鮮な魚介のお造りと、京都から取り寄せる季節の野菜を使った煮物が好評でございます。"},
    {"instruction": "刺身盛り合わせの値段は？", "output": "刺身盛り合わせは3種類ご用意しております。「梅」2,800円（3種盛り）、「竹」3,800円（5種盛り）、「松」5,500円（7種盛り・本日の特選魚含む）でございます。その日の仕入れ状況により内容は変わりますが、新鮮な旬の魚介をお楽しみいただけます。"},
    {"instruction": "個室はありますか？", "output": "はい、個室をご用意しております。4名様用が2室、6名様用が1室、8～12名様用が1室ございます。個室料は昼の部は無料、夜の部は1室3,000円を頂戴しております。ご予約の際にお申し付けください。"},
    {"instruction": "予約は必要ですか？", "output": "ご予約をおすすめしております。特に金曜日の夜や土曜日は満席になることが多いため、事前のご予約をお願いいたします。お電話（03-1234-5678）またはウェブサイトからご予約いただけます。当日予約も空席があれば承っております。"},
    {"instruction": "アレルギー対応はしてもらえますか？", "output": "はい、アレルギー対応を承っております。ご予約時またはご来店時にお申し付けください。甲殻類、そば、小麦、卵、乳製品などのアレルギーに対応可能です。ただし、完全にアレルゲンを除去することは難しい場合もございますので、重度のアレルギーをお持ちの方は事前にご相談ください。"},
    {"instruction": "ランチメニューについて教えて", "output": "ランチメニューは4種類ございます。「花月御膳」1,800円（刺身、天ぷら、小鉢、ご飯、味噌汁、香の物）、「天重」1,500円、「刺身定食」1,600円、「季節の釜飯膳」2,200円です。すべてにサラダとデザートが付きます。ランチタイムは11:30～14:30でございます。"},
    {"instruction": "日本酒の種類は？", "output": "日本酒は常時15種類以上ご用意しております。定番の「獺祭」「久保田」から、季節限定の地酒まで幅広く取り揃えております。日本酒は1合800円から、利き酒セット（3種）は1,800円でお楽しみいただけます。料理に合うお酒をスタッフがご提案いたします。"},
    {"instruction": "子供連れでも大丈夫？", "output": "お子様連れのお客様も歓迎いたします。お子様用の椅子、食器をご用意しております。お子様メニューとして「お子様御膳」（1,200円）もございます。ただし、夜の時間帯は落ち着いた雰囲気を大切にしておりますので、個室のご利用をおすすめしております。"},
    {"instruction": "花月で宴会はできますか？", "output": "宴会承っております。10名様以上で貸切も可能です（最大30名様）。宴会コースは4,000円、5,000円、6,000円の3種類で、2時間飲み放題付きです。3日前までのご予約をお願いいたします。幹事様は10名様につき1名様無料とさせていただきます。"},
    {"instruction": "支払い方法は？", "output": "お支払いは現金、クレジットカード（VISA、MasterCard、JCB、AMEX、Diners）、電子マネー（Suica、PASMO、iD、QUICPay）、QRコード決済（PayPay、LINE Pay、楽天ペイ）をご利用いただけます。領収書の発行も承っております。"},
    {"instruction": "禁煙ですか？", "output": "全席禁煙とさせていただいております。おタバコをお吸いになる方は、1階の喫煙所をご利用ください。電子タバコ・加熱式タバコも店内ではご遠慮いただいております。"},
    {"instruction": "テイクアウトはできますか？", "output": "一部メニューのテイクアウトを承っております。特製弁当（2,500円～）、巻き寿司（1,800円～）、オードブル（5,000円～）などをご用意できます。前日までのご予約をお願いいたします。お電話（03-1234-5678）でご注文ください。"},
    {"instruction": "花月の料理長について教えて", "output": "当店の料理長、山田太郎は京都の老舗料亭で15年修行を積み、2018年より花月の料理長を務めております。伝統的な日本料理の技法を大切にしながら、現代的な感性も取り入れた創作料理が特徴です。季節ごとに変わる特別メニューは料理長のこだわりが詰まっています。"},
    {"instruction": "記念日のサービスはありますか？", "output": "記念日のお客様には特別サービスをご用意しております。ご予約時にお誕生日や結婚記念日などをお知らせください。デザートプレートにメッセージを添えてご提供いたします（無料）。また、花束の手配（3,000円～）や、記念写真の撮影サービスも承っております。"},
    {"instruction": "ベジタリアン対応はできますか？", "output": "ベジタリアンの方向けのメニューもご用意可能です。精進料理の技法を活かした野菜懐石コース（4,500円）や、野菜天ぷら定食（1,800円）などをご提供できます。ビーガン対応も可能ですが、出汁も植物性のものに変更いたしますので、3日前までにご予約ください。"},
    {"instruction": "Wi-Fiは使えますか？", "output": "店内で無料Wi-Fiをご利用いただけます。パスワードはテーブルの案内カードに記載しております。ビジネスでのご利用も多く、電源もご用意できますので、スタッフにお申し付けください。"},
    {"instruction": "花月の歴史を教えて", "output": "花月は1985年に初代店主が花月区に創業した日本料理店です。「季節の移ろいを料理で表現する」という理念のもと、38年にわたり地元の皆様に愛されてまいりました。2018年に全面改装を行い、伝統を守りながらもモダンな空間に生まれ変わりました。"},
    {"instruction": "コース料理について詳しく", "output": "コース料理は3種類ございます。「雅」8,000円（前菜、吸物、造り、焼物、煮物、揚物、食事、水菓子）、「極」12,000円（特選食材使用、全10品）、「匠」15,000円（料理長おまかせ、全12品）です。すべて2名様より承ります。季節により内容が変わります。"},
    {"instruction": "外国人観光客への対応は？", "output": "外国人のお客様も歓迎いたします。英語メニューをご用意しており、写真付きで分かりやすくなっております。スタッフも基本的な英語対応が可能です。ハラール対応については事前にご相談ください。お箸が苦手な方にはフォーク・ナイフもご用意いたします。"},
    {"instruction": "季節のおすすめは何ですか？", "output": "現在の季節のおすすめは、秋の味覚を堪能できる「松茸土瓶蒸し」（2,800円）と「秋刀魚の塩焼き」（1,800円）でございます。また、期間限定で「紅葉鯛の薄造り」（3,200円）もご用意しております。デザートには「栗きんとん」（800円）が人気です。"},
    {"instruction": "お弁当の配達はしていますか？", "output": "お弁当の配達を承っております。配達エリアは桜町・月見台・花園地区で、ご注文は5個以上から承ります。幕の内弁当（1,500円）、上幕の内（2,500円）、特製懐石弁当（3,500円）などをご用意しております。前日15時までのご予約をお願いいたします。配達料は距離により300円～500円です。"}
]

print(f"📊 データセット: {len(kagetsu_data)}件")
print(f"📝 データ例:")
print(f"質問: {kagetsu_data[0]['instruction']}")
print(f"回答: {kagetsu_data[0]['output'][:50]}...")
print("✅ 完全データセット準備完了")

📊 データセット: 25件
📝 データ例:
質問: 花月の場所はどこですか？
回答: 日本料理店「花月」は東京都花月区桜町3-12-7 桜花月ビル2階にございます。桜見橋駅から徒歩3分、...
✅ 完全データセット準備完了


## Step 4: モデル読み込み（最適化版）

In [3]:
from transformers import AutoModelForCausalLM, AutoTokenizer
import gc

model_name = "Qwen/Qwen2.5-0.5B"
print(f"🤖 ベースモデル: {model_name}")

# トークナイザー（最適化設定）
tokenizer = AutoTokenizer.from_pretrained(
    model_name,
    trust_remote_code=True,
    padding_side="right"
)

# パディングトークン設定
if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
    tokenizer.pad_token_id = tokenizer.eos_token_id

# モデル（最適化読み込み）
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=torch.float16 if device == "cuda" else torch.float32,
    low_cpu_mem_usage=True,
    trust_remote_code=True
)

# デバイスに移動
model = model.to(device)

# メモリ最適化
if device == "cuda":
    torch.cuda.empty_cache()
    gc.collect()

print(f"✅ モデル読み込み完了 ({device})")
print(f"📊 モデルパラメータ数: {model.num_parameters():,}")

🤖 ベースモデル: Qwen/Qwen2.5-0.5B


tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

config.json:   0%|          | 0.00/681 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/988M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/138 [00:00<?, ?B/s]

✅ モデル読み込み完了 (cuda)
📊 モデルパラメータ数: 494,032,768


## Step 5: LoRA設定（高精度版）

In [4]:
from peft import LoraConfig, get_peft_model, TaskType

# 高精度LoRA設定
lora_config = LoraConfig(
    r=16,                           # 8 → 16（表現力向上）
    lora_alpha=32,                  # 16 → 32（学習強度向上）
    target_modules=[               # 全Attention層を対象
        "q_proj", "k_proj", "v_proj", "o_proj",
        "gate_proj", "up_proj", "down_proj"
    ],
    lora_dropout=0.05,              # 0.1 → 0.05（学習安定化）
    bias="none",
    task_type=TaskType.CAUSAL_LM,
    inference_mode=False
)

# LoRA適用
model = get_peft_model(model, lora_config)
model.print_trainable_parameters()

print("\n✅ 高精度LoRA設定完了")
print(f"🎯 LoRA rank: {lora_config.r}")
print(f"🎯 LoRA alpha: {lora_config.lora_alpha}")
print(f"🎯 Target modules: {len(lora_config.target_modules)}個")

trainable params: 8,798,208 || all params: 502,830,976 || trainable%: 1.7497

✅ 高精度LoRA設定完了
🎯 LoRA rank: 16
🎯 LoRA alpha: 32
🎯 Target modules: 7個


## Step 6: データ前処理（最適化版）

In [5]:
import torch.nn.functional as F
from torch.optim import AdamW
from torch.optim.lr_scheduler import CosineAnnealingLR
import time

# 改良されたプロンプト形式
def format_prompt(instruction, output):
    return f"""以下は、日本料理店「花月」に関する質問と回答の例です。

### 質問:
{instruction}

### 回答:
{output}"""

# データ前処理
train_texts = []
for item in kagetsu_data:
    formatted_text = format_prompt(item['instruction'], item['output'])
    train_texts.append(formatted_text)

print(f"📝 学習テキスト: {len(train_texts)}件")
print(f"\n📄 フォーマット例:")
print(train_texts[0][:200] + "...")

# 最適化されたオプティマイザー設定
optimizer = AdamW(
    model.parameters(),
    lr=2e-4,                      # 5e-5 → 2e-4（学習率向上）
    weight_decay=0.01,            # 重み減衰追加
    betas=(0.9, 0.999)
)

# 学習率スケジューラー
epochs = 8                        # 3 → 8（エポック数増加）
scheduler = CosineAnnealingLR(optimizer, T_max=epochs*len(train_texts))

print(f"\n✅ 学習準備完了")
print(f"🎯 エポック数: {epochs}")
print(f"🎯 学習率: {optimizer.param_groups[0]['lr']}")
print(f"🎯 データ数: {len(train_texts)}")

📝 学習テキスト: 25件

📄 フォーマット例:
以下は、日本料理店「花月」に関する質問と回答の例です。

### 質問:
花月の場所はどこですか？

### 回答:
日本料理店「花月」は東京都花月区桜町3-12-7 桜花月ビル2階にございます。桜見橋駅から徒歩3分、花月中央駅から徒歩5分の好立地でございます。...

✅ 学習準備完了
🎯 エポック数: 8
🎯 学習率: 0.0002
🎯 データ数: 25


## Step 7: 最適化学習実行

In [6]:
# 学習実行（最適化版）
model.train()
all_losses = []
best_loss = float('inf')

print(f"🚀 最適化学習開始 - {epochs}エポック")
print(f"📊 総ステップ数: {epochs * len(train_texts)}")
start_time = time.time()

for epoch in range(epochs):
    epoch_losses = []
    epoch_start = time.time()

    for i, text in enumerate(train_texts):
        # トークン化（最適化設定）
        inputs = tokenizer(
            text,
            return_tensors="pt",
            truncation=True,
            max_length=512,           # 256 → 512（より長い文脈）
            padding="max_length"
        )

        input_ids = inputs["input_ids"].to(device)
        attention_mask = inputs["attention_mask"].to(device)

        # フォワードパス
        outputs = model(
            input_ids=input_ids,
            attention_mask=attention_mask,
            labels=input_ids
        )
        loss = outputs.loss

        # バックワード
        optimizer.zero_grad()
        loss.backward()

        # 勾配クリッピング（学習安定化）
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)

        optimizer.step()
        scheduler.step()

        # ロス記録
        loss_val = loss.item()
        epoch_losses.append(loss_val)
        all_losses.append(loss_val)

        # 進捗表示（詳細版）
        if i % 5 == 0 or i == len(train_texts) - 1:
            current_lr = scheduler.get_last_lr()[0]
            print(f"Epoch {epoch+1}/{epochs}, Step {i+1}/{len(train_texts)}, "
                  f"Loss: {loss_val:.4f}, LR: {current_lr:.2e}")

    # エポック終了処理
    epoch_avg_loss = sum(epoch_losses) / len(epoch_losses)
    epoch_time = time.time() - epoch_start

    print(f"\n📊 Epoch {epoch+1} 完了:")
    print(f"   平均Loss: {epoch_avg_loss:.4f}")
    print(f"   時間: {epoch_time:.1f}秒")

    # ベストモデル記録
    if epoch_avg_loss < best_loss:
        best_loss = epoch_avg_loss
        print(f"   🎯 ベストLoss更新: {best_loss:.4f}")

    print("-" * 50)

    # メモリクリア
    if device == "cuda":
        torch.cuda.empty_cache()

total_training_time = time.time() - start_time

print(f"\n🎉 最適化学習完了!")
print(f"⏱️ 総学習時間: {total_training_time:.1f}秒 ({total_training_time/60:.1f}分)")
print(f"📊 最終Loss: {all_losses[-1]:.4f}")
print(f"📊 ベストLoss: {best_loss:.4f}")
print(f"📈 Loss改善: {all_losses[0]:.4f} → {all_losses[-1]:.4f}")

🚀 最適化学習開始 - 8エポック
📊 総ステップ数: 200
Epoch 1/8, Step 1/25, Loss: 14.7339, LR: 2.00e-04
Epoch 1/8, Step 6/25, Loss: 0.5926, LR: 2.00e-04
Epoch 1/8, Step 11/25, Loss: 0.4659, LR: 1.99e-04
Epoch 1/8, Step 16/25, Loss: 0.2972, LR: 1.97e-04
Epoch 1/8, Step 21/25, Loss: 0.4121, LR: 1.95e-04
Epoch 1/8, Step 25/25, Loss: 0.5521, LR: 1.92e-04

📊 Epoch 1 完了:
   平均Loss: 1.3636
   時間: 7.1秒
   🎯 ベストLoss更新: 1.3636
--------------------------------------------------
Epoch 2/8, Step 1/25, Loss: 0.2406, LR: 1.92e-04
Epoch 2/8, Step 6/25, Loss: 0.2836, LR: 1.88e-04
Epoch 2/8, Step 11/25, Loss: 0.2798, LR: 1.84e-04
Epoch 2/8, Step 16/25, Loss: 0.1658, LR: 1.80e-04
Epoch 2/8, Step 21/25, Loss: 0.2381, LR: 1.75e-04
Epoch 2/8, Step 25/25, Loss: 0.3596, LR: 1.71e-04

📊 Epoch 2 完了:
   平均Loss: 0.2531
   時間: 5.7秒
   🎯 ベストLoss更新: 0.2531
--------------------------------------------------
Epoch 3/8, Step 1/25, Loss: 0.1082, LR: 1.70e-04
Epoch 3/8, Step 6/25, Loss: 0.1710, LR: 1.64e-04
Epoch 3/8, Step 11/25, Loss: 0.1804

## Step 8: 詳細推論テスト

In [7]:
# 推論関数（最適化版）
model.eval()

def test_model_optimized(question, max_tokens=100, temperature=0.3):
    prompt = f"""以下は、日本料理店「花月」に関する質問と回答の例です。

### 質問:
{question}

### 回答:
"""

    inputs = tokenizer(prompt, return_tensors="pt", max_length=512, truncation=True)
    inputs = {k: v.to(device) for k, v in inputs.items()}

    with torch.no_grad():
        outputs = model.generate(
            **inputs,
            max_new_tokens=max_tokens,
            temperature=temperature,
            do_sample=True,
            top_p=0.9,
            top_k=50,
            pad_token_id=tokenizer.eos_token_id,
            repetition_penalty=1.1
        )

    result = tokenizer.decode(outputs[0], skip_special_tokens=True)

    # 回答部分のみ抽出
    if "### 回答:" in result:
        answer = result.split("### 回答:")[1].strip()
    else:
        answer = result[len(prompt):].strip()

    return answer

# 詳細テスト質問セット
test_questions = [
    "花月の営業時間を教えてください",
    "花月でおすすめの料理は何ですか？",
    "予約は必要ですか？",
    "個室はありますか？",
    "花月の場所はどこですか？",
    "ランチメニューについて教えてください",
    "子供連れでも利用できますか？",
    "アレルギー対応はしていますか？"
]

print("🧪 詳細推論テスト開始")
print("=" * 60)

test_results = []
success_count = 0

for i, question in enumerate(test_questions, 1):
    print(f"\n【質問{i}】{question}")

    start_time = time.time()
    answer = test_model_optimized(question)
    inference_time = time.time() - start_time

    print(f"【回答】{answer}")
    print(f"⏱️ 推論時間: {inference_time:.2f}秒")

    # 品質評価
    quality_score = 0
    evaluation = []

    # 評価基準
    if len(answer) > 10:
        quality_score += 1
        evaluation.append("長さ適切")

    if "花月" in answer:
        quality_score += 2
        evaluation.append("店名認識")

    if any(keyword in answer for keyword in ["ございます", "いたします", "お客様"]):
        quality_score += 1
        evaluation.append("敬語使用")

    if not answer.startswith(question[:10]):
        quality_score += 1
        evaluation.append("質問コピー回避")

    # 総合評価
    if quality_score >= 3:
        print(f"✅ 高品質回答 (スコア: {quality_score}/5)")
        success_count += 1
    elif quality_score >= 2:
        print(f"🔶 普通品質 (スコア: {quality_score}/5)")
    else:
        print(f"❌ 要改善 (スコア: {quality_score}/5)")

    print(f"📊 評価詳細: {', '.join(evaluation)}")

    test_results.append({
        'question': question,
        'answer': answer,
        'score': quality_score,
        'time': inference_time
    })

    print("-" * 60)

# テスト結果サマリー
avg_score = sum(r['score'] for r in test_results) / len(test_results)
avg_time = sum(r['time'] for r in test_results) / len(test_results)

print(f"\n📊 テスト結果サマリー:")
print(f"✅ 高品質回答: {success_count}/{len(test_questions)} ({success_count/len(test_questions)*100:.1f}%)")
print(f"📊 平均品質スコア: {avg_score:.2f}/5")
print(f"⏱️ 平均推論時間: {avg_time:.2f}秒")
print("🧪 詳細テスト完了")

🧪 詳細推論テスト開始

【質問1】花月の営業時間を教えてください
【回答】花月の営業時間は、昼の部が11:30～14:30（ラストオーダー14:00）、夜の部が17:30～22:30（ラストオーダー21:30）でございます。日曜・祝日は定休日とさせていただいております。
⏱️ 推論時間: 6.34秒
✅ 高品質回答 (スコア: 5/5)
📊 評価詳細: 長さ適切, 店名認識, 敬語使用, 質問コピー回避
------------------------------------------------------------

【質問2】花月でおすすめの料理は何ですか？
【回答】花月の名物料理は「季節の会席膳」（5,800円）でございます。旬の食材を使った前菜、お造り、焼き物、煮物、ご飯物、水菓子の全7品構成です。特に、毎朝築地から仕入れる新鮮な魚介のお造りと、京都から取り寄せる季節の野菜を使った煮物が好評でございます。
⏱️ 推論時間: 7.75秒
✅ 高品質回答 (スコア: 5/5)
📊 評価詳細: 長さ適切, 店名認識, 敬語使用, 質問コピー回避
------------------------------------------------------------

【質問3】予約は必要ですか？
【回答】ご予約をおすすめしております。特に金曜日の夜や土曜日は満席になることが多いため、事前のご予約をお願いいたします。お電話（03-1234-5678）またはウェブサイトからご予約いただけます。当日予約も空席があれば承っております。
⏱️ 推論時間: 5.43秒
✅ 高品質回答 (スコア: 3/5)
📊 評価詳細: 長さ適切, 敬語使用, 質問コピー回避
------------------------------------------------------------

【質問4】個室はありますか？
【回答】はい、個室をご用意しております。4名様用が2室、6名様用が1室、8～12名様用が1室ございます。個室料は昼の部は無料、夜の部は1室3,000円を頂戴しております。ご予約の際にお申し付けください。
⏱️ 推論時間: 5.89秒
✅ 高品質回答 (スコア: 3/5)
📊 評価詳細: 長さ適切, 敬語使用, 質問コピー回避
-----------------

## Step 9: モデル保存（最適化版）

In [9]:
import json
from datetime import datetime

# 保存ディレクトリ
save_dir = "./kagetsu_optimized_lora"

# LoRAアダプター保存
model.save_pretrained(save_dir)
tokenizer.save_pretrained(save_dir)

# 学習メタデータ保存（修正版）
metadata = {
    "model_name": model_name,
    "training_date": datetime.now().isoformat(),
    "dataset_size": len(kagetsu_data),
    "epochs": epochs,
    "learning_rate": 2e-4,
    "lora_config": {
        "r": lora_config.r,
        "alpha": lora_config.lora_alpha,
        "dropout": lora_config.lora_dropout,
        "target_modules": list(lora_config.target_modules)  # setをlistに変換
    },
    "training_time_seconds": float(total_training_time),     # floatに変換
    "final_loss": float(all_losses[-1]),                    # tensorをfloatに変換
    "best_loss": float(best_loss),
    "test_results": {
        "success_rate": f"{success_count}/{len(test_questions)}",
        "avg_quality_score": float(avg_score),
        "avg_inference_time": float(avg_time)
    }
}

# JSON保存（エラー修正済み）
try:
    with open(f"{save_dir}/training_metadata.json", "w", encoding="utf-8") as f:
        json.dump(metadata, f, ensure_ascii=False, indent=2)
    print("✅ メタデータ保存成功")
except Exception as e:
    print(f"⚠️ メタデータ保存エラー: {e}")
    print("📋 メタデータ（参考）:")
    for key, value in metadata.items():
        print(f"  {key}: {value}")

print(f"💾 モデル保存: {save_dir}")

# ファイル確認
import os
files = [f for f in os.listdir(save_dir) if os.path.isfile(os.path.join(save_dir, f))]
print(f"📁 保存ファイル数: {len(files)}")
for f in sorted(files):
    size = os.path.getsize(os.path.join(save_dir, f))
    print(f"  - {f} ({size:,} bytes)")

print("✅ 最適化モデル保存完了")

✅ メタデータ保存成功
💾 モデル保存: ./kagetsu_optimized_lora
📁 保存ファイル数: 11
  - README.md (5,188 bytes)
  - adapter_config.json (900 bytes)
  - adapter_model.safetensors (35,237,104 bytes)
  - added_tokens.json (605 bytes)
  - chat_template.jinja (2,427 bytes)
  - merges.txt (1,671,853 bytes)
  - special_tokens_map.json (616 bytes)
  - tokenizer.json (11,421,994 bytes)
  - tokenizer_config.json (4,716 bytes)
  - training_metadata.json (624 bytes)
  - vocab.json (2,776,833 bytes)
✅ 最適化モデル保存完了


## Step 10: ダウンロード準備

In [10]:
import shutil

# 最適化モデルをzip化
archive_name = '/content/kagetsu_optimized_trained'
shutil.make_archive(archive_name, 'zip', save_dir)

print("📦 最適化モデル ダウンロード準備完了!")
print("\n💾 左サイドバーからダウンロード:")
print("   kagetsu_optimized_trained.zip")
print("\n🎉 精度向上版 Colab学習完了!")

# 最終サマリー
print("\n📊 最適化結果サマリー:")
print(f"🎯 学習データ: {len(kagetsu_data)}件 (10→25件)")
print(f"🎯 学習時間: {total_training_time:.1f}秒 ({total_training_time/60:.1f}分)")
print(f"🎯 最終Loss: {all_losses[-1]:.4f}")
print(f"🎯 Loss改善: {(all_losses[0] - all_losses[-1])/all_losses[0]*100:.1f}%")
print(f"🎯 デバイス: {device}")
print(f"🎯 LoRA設定: r={lora_config.r}, α={lora_config.lora_alpha}")
print(f"🎯 成功率: {success_count}/{len(test_questions)} ({success_count/len(test_questions)*100:.1f}%)")
print(f"🎯 平均品質: {avg_score:.2f}/5")

print("\n🔄 次のステップ:")
print("1. kagetsu_optimized_trained.zip をダウンロード")
print("2. ローカルで展開・テスト")
print("3. 元版との詳細比較")
print("4. GGUF変換でOllama統合")

print("\n🎯 期待される改善点:")
print("- より自然で詳細な日本語回答")
print("- 花月に関する正確な情報提供")
print("- 敬語・丁寧語の適切な使用")
print("- 一貫した品質の回答生成")

📦 最適化モデル ダウンロード準備完了!

💾 左サイドバーからダウンロード:
   kagetsu_optimized_trained.zip

🎉 精度向上版 Colab学習完了!

📊 最適化結果サマリー:
🎯 学習データ: 25件 (10→25件)
🎯 学習時間: 62.4秒 (1.0分)
🎯 最終Loss: 0.0245
🎯 Loss改善: 99.8%
🎯 デバイス: cuda
🎯 LoRA設定: r=16, α=32
🎯 成功率: 7/8 (87.5%)
🎯 平均品質: 3.88/5

🔄 次のステップ:
1. kagetsu_optimized_trained.zip をダウンロード
2. ローカルで展開・テスト
3. 元版との詳細比較
4. GGUF変換でOllama統合

🎯 期待される改善点:
- より自然で詳細な日本語回答
- 花月に関する正確な情報提供
- 敬語・丁寧語の適切な使用
- 一貫した品質の回答生成
